In [1]:
pip install topicmodeltuner

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.0/60.0 kB 6.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.4/143.4 kB 15.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.2/5.2 MB 43.9 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.2/88.2 kB 10.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 10.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.1/7.1 MB 79.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 73.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 26.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [2]:
from topictuner import TopicModelTuner as TMT
from sklearn.datasets import fetch_20newsgroups

2023-06-05 17:28:53.063 | INFO     | topictuner:<module>:7 - cuML not present - cumlTopicModelTuner not avaialable


Get 20NewsGroup data

In [3]:
docs = fetch_20newsgroups(subset='all',  remove=('headers', 'footers', 'quotes'))['data']

Create a TMT instance from scratch

In [4]:
tmt = TMT(verbose=2) # verbose turns tqdm on

Alternatively, you can create one from an existing BERTopic instance by calling 

newTMT = TMT.wrapBERTopicModel(\<your BERTopic model\>)

Create the embeddings.

In [5]:
tmt.createEmbeddings(docs)

Then reduce them to 5 features ala BERTopic by calling TMT.reduce()

In [6]:
tmt.reduce()

UMAP(angular_rp_forest=True, metric='cosine', min_dist=0.0, n_components=5, n_neighbors=5, random_state=875622, verbose=2)
Mon Jun  5 18:09:17 2023 Construct fuzzy simplicial set
Mon Jun  5 18:09:17 2023 Finding Nearest Neighbors
Mon Jun  5 18:09:17 2023 Building RP forest with 12 trees
Mon Jun  5 18:09:23 2023 NN descent for 14 iterations
	 1  /  14
	 2  /  14
	 3  /  14
	 4  /  14
	 5  /  14
	 6  /  14
	 7  /  14
	 8  /  14
	Stopping threshold met -- exiting after 8 iterations
Mon Jun  5 18:09:43 2023 Finished Nearest Neighbor Search
Mon Jun  5 18:09:47 2023 Construct embedding


Epochs completed:   0%|            0/200 [00:00]

Mon Jun  5 18:10:00 2023 Finished embedding


Now we can explore different HDBSCAN settings for this instance of the UMAP reductions.

There are four search functions - `randomSearch`, `psuedoGridSearch`, `simpleSearch`, and `gridSearch`. All four take a list of `min_cluster_sizes` as the first argument. The first four search methods taketwo lists as input. The first is the `min_cluster_size` arguments. The second argument for `randomSearch` and `psuedoGridSearch` is a list of floats where each values <= 1. In these first two search methods values for the second list are used to multiply with a corresponding value from the first list to produce a valid integer value for the `sample_size` parameter. Examples follow below.

For simpleSearch the second array is a list of min_sample values that corresponds 1:1 with the first list of `min_cluster_size` values. With gridSearch you just provide the values of the `min_cluster_sizes` you are interested in and then searches are run for every possible sample_size value.

Typically you will do an initial narrowing of the search using `randomSearch`. `randomSearch` has a third parameter for the number of searches that will be run from the values provided and defaults to 20. All the other searches will exhaust whatever parameters are passed. Once you've narrowed down with `randomSearch` you can further narrow down with the remaining searches. Be aware that there can be a non-linear relationship between different setting pairs. For example, just because settings of 125,30 provide better results than say, 200,100, it may be that 215,22 work best. Running these searches is reasonably cheap computationally speaking, and `randomSearch` will generally give you a "lay of the land" so you can make judgements about where to focus your efforts.

Each search method returns a sorted DataFrame with that passes results. All the results for any session are aggregated in the `TMT.ResultsDF` DataFrame. `TMT.summarizeResults(`) will summarize the ResultsDF DataFrame or you can pass it your interim results and then it will summarize those for you. See below for examples.

In the next cell 20 random searches will be run using randomly chosen `min_cluster_size` values between 120 and 150. The corresponding `sample_size` values will be generated by randomly selecting one of the percentage multipliers and calculating the appropriate `sample_size` value for that `min_cluster_size`.

In [7]:
lastRunResultsDF = tmt.randomSearch([*range(30,151)], [.1, .25, .5, .75, 1])

  0%|          | 0/20 [00:00<?, ?it/s]

`lastRunResultsDF` is a dataframe containing the results from the 20 searches just completed

TMT.visualizeSearch produces a plotly parallel coordinates graph. You can pass it TMT.ResultsDF to get a view of all the searches, or pass it the results from a particular search.

In [8]:
lastRunResultsDF

min_cluster_size  min_samples  number_of_clusters  number_uncategorized
0                140           35                  16                  1546
1                122           30                  29                  3470
2                 71           53                  39                  4343
3                 53            5                  72                  3591
4                139          104                  16                  2697
5                 31            7                 150                  5110
6                 63            6                  50                  2945
7                105           10                  37                  3091
8                 97           48                  31                  4021
9                 84            8                  43                  2699
10                39           19                  89                  5325
11                39            9                 105                  4666
12                37            3                 137                  4860
13                94           47                  33                  4415
14                51           12                  68                  3883
15                97            9                  39                  3006
16                95           71                  19                  2705
17                92           46                  31                  3884
18               113          113                  16                  3230
19                46           23                  50                  3435

The cell below runs psuedoGridSearch for all values from 62 to 70 with `sample_size` values at 10% to 100% of each of the `min_cluster_size` values.

In [10]:
lastRunResultsDF = tmt.pseudoGridSearch([*range(62,71)], [x/100 for x in range(10,101,10)])

  0%|          | 0/90 [00:00<?, ?it/s]

The immediate results of the above search will be contained in lastRunResultsDF. You can see a summary DataFrame using the `TMT.summarizeResult()` method.

In [11]:
tmt.summarizeResults(lastRunResultsDF)

min_cluster_size  min_samples  number_of_clusters  number_uncategorized
0                 69           69                  22                  2304
1                 70           42                  23                  1892
2                 70           35                  24                  1597
3                 64           38                  26                  2449
4                 64           64                  36                  4154
5                 66           66                  37                  4641
6                 63           63                  38                  4775
7                 70           49                  39                  4316
8                 64           57                  40                  4366
9                 62           55                  41                  4288
10                62           49                  42                  4472
11                69           34                  43                  3842
12                67           20                  44                  3575
13                70            7                  45                  2895
14                62           18                  46                  3068
15                69            6                  47                  2868
16                64            6                  48                  2895
17                62            6                  50                  2945
18                62           12                  55                  3781

If you call summarizeResults() without explicitly passing a DataFrame it will use the internal TMT.ResultsDF DataFrame which contains all the search results run this session.

In [12]:
tmt.summarizeResults()

min_cluster_size  min_samples  number_of_clusters  number_uncategorized
1                140           35                  16                  1546
2                 95           71                  19                  2705
4                 69           69                  22                  2304
6                 70           42                  23                  1892
5                 70           35                  24                  1597
7                 64           38                  26                  2449
8                122           30                  29                  3470
9                 92           46                  31                  3884
10                94           47                  33                  4415
11                64           64                  36                  4154
12               105           10                  37                  3091
13                63           63                  38                  4775
14                97            9                  39                  3006
15                64           57                  40                  4366
16                62           55                  41                  4288
17                62           49                  42                  4472
18                84            8                  43                  2699
19                67           20                  44                  3575
20                70            7                  45                  2895
21                62           18                  46                  3068
22                69            6                  47                  2868
23                64            6                  48                  2895
24                63            6                  50                  2945
25                62           12                  55                  3781
26                51           12                  68                  3883
27                53            5                  72                  3591
28                39           19                  89                  5325
29                39            9                 105                  4666
0                 37            3                 137                  4860
3                 31            7                 150                  5110

`TMT.summarizeResults` sorts a results table by number_of_cluster and selects the 'best' value for that number of clusters by choosing the one with the least uncategorized results. You can sort the DataFrame by whatever value interests you.

In [13]:
tmt.summarizeResults(lastRunResultsDF).sort_values(by=['number_uncategorized'])

min_cluster_size  min_samples  number_of_clusters  number_uncategorized
2                 70           35                  24                  1597
1                 70           42                  23                  1892
0                 69           69                  22                  2304
3                 64           38                  26                  2449
15                69            6                  47                  2868
16                64            6                  48                  2895
13                70            7                  45                  2895
17                62            6                  50                  2945
14                62           18                  46                  3068
12                67           20                  44                  3575
18                62           12                  55                  3781
11                69           34                  43                  3842
4                 64           64                  36                  4154
9                 62           55                  41                  4288
7                 70           49                  39                  4316
8                 64           57                  40                  4366
10                62           49                  42                  4472
5                 66           66                  37                  4641
6                 63           63                  38                  4775

There are further visual aids to help you find the best parameters for your model. `TMT.visualizeSearch`, like `summarizeResults`, can be called against a subset of the searches performed or against the entire search space.

In [14]:
tmt.visualizeSearch(lastRunResultsDF).show()

TMT can generate a scatterplot of your embeddings overlayed with the clustering of a given set of parameters. This can assist in deciding how many clusters to select for your model.

To accomplish this, first you must create a 2D reduction of the embeddings suitable for a 2D scatterplot. The default 2D reduction method is UMAP, but you can also specify TSNE. (You can also use your own 2D reduction by simply setting `TMT.viz_reduction`.)

In [15]:
tmt.createVizReduction('TSNE')

[t-SNE] Computing 91 nearest neighbors...
[t-SNE] Indexed 18846 samples in 0.004s...
[t-SNE] Computed neighbors for 18846 samples in 14.240s...
[t-SNE] Computed conditional probabilities for sample 1000 / 18846
[t-SNE] Computed conditional probabilities for sample 2000 / 18846
[t-SNE] Computed conditional probabilities for sample 3000 / 18846
[t-SNE] Computed conditional probabilities for sample 4000 / 18846
[t-SNE] Computed conditional probabilities for sample 5000 / 18846
[t-SNE] Computed conditional probabilities for sample 6000 / 18846
[t-SNE] Computed conditional probabilities for sample 7000 / 18846
[t-SNE] Computed conditional probabilities for sample 8000 / 18846
[t-SNE] Computed conditional probabilities for sample 9000 / 18846
[t-SNE] Computed conditional probabilities for sample 10000 / 18846
[t-SNE] Computed conditional probabilities for sample 11000 / 18846
[t-SNE] Computed conditional probabilities for sample 12000 / 18846
[t-SNE] Computed conditional probabilities for sa

Once there is a 2D representation of the embeddings you can view them using different values for the HDBSCAN parameters.

In [16]:
tmt.visualizeEmbeddings(131,78).show()

You can save your TMT model with TMT.save()

In [17]:
tmt.save('temp')

Mon Jun  5 18:20:57 2023 Worst tree score: 0.16645442
Mon Jun  5 18:20:57 2023 Mean tree score: 0.17815894
Mon Jun  5 18:20:57 2023 Best tree score: 0.19224239
Mon Jun  5 18:21:01 2023 Forward diversification reduced edges from 94230 to 65127
Mon Jun  5 18:21:05 2023 Reverse diversification reduced edges from 65127 to 65127


/usr/local/lib/python3.10/dist-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning:

Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.



Mon Jun  5 18:21:10 2023 Degree pruning reduced edges from 64100 to 63471
Mon Jun  5 18:21:10 2023 Resorting data and graph based on tree order
Mon Jun  5 18:21:10 2023 Building and compiling search function


And restore it using TMT.load()

In [18]:
tmt2 = TMT.load('temp')

Mon Jun  5 18:21:14 2023 Building and compiling search function


Once you have determined parameters that work for your text, TMT can manufacture a BERTopic model. Note in this example we pass BERTopic the embeddings created earlier - no need to have BERTopic re-run them. (Although BERTopic will rerun UMAP).

In [19]:
bt1 = tmt2.getBERTopicModel(131, 24)
bt1.fit_transform(tmt2.docs, tmt2.embeddings)
bt1.get_topic_info()

UMAP(angular_rp_forest=True, metric='cosine', min_dist=0.0, n_components=5, n_neighbors=5, random_state=875622, verbose=2)
Mon Jun  5 18:23:50 2023 Construct fuzzy simplicial set
Mon Jun  5 18:23:50 2023 Finding Nearest Neighbors
Mon Jun  5 18:23:50 2023 Building RP forest with 12 trees
Mon Jun  5 18:23:50 2023 NN descent for 14 iterations
	 1  /  14
	 2  /  14
	 3  /  14
	 4  /  14
	 5  /  14
	 6  /  14
	 7  /  14
	 8  /  14
	Stopping threshold met -- exiting after 8 iterations
Mon Jun  5 18:23:51 2023 Finished Nearest Neighbor Search
Mon Jun  5 18:23:51 2023 Construct embedding


Epochs completed:   0%|            0/200 [00:00]

Mon Jun  5 18:24:13 2023 Finished embedding


Topic  Count                       Name  \
0      -1   3089           -1_ax_max_the_to   
1       0   1954           0_of_the_that_to   
2       1   1829           1_the_he_game_in   
3       2   1653            2_the_to_and_it   
4       3   1328            3_the_of_to_and   
5       4    785           4_the_to_that_of   
6       5    769            5_of_the_to_and   
7       6    713            6_the_to_key_be   
8       7    706         7_for_the_and_with   
9       8    610       8_image_jpeg_and_for   
10      9    542   9_ken_ockey__too__accent   
11     10    500            10_00_50_for_10   
12     11    446           11_gun_the_of_to   
13     12    434  12_card_monitor_the_video   
14     13    409     13_scsi_drive_ide_disk   
15     14    380   14_israel_the_of_israeli   
16     15    276    15_window_the_to_widget   
17     16    269  16_that_of_the_homosexual   
18     17    237           17_the_of_and_in   
19     18    234          18_that_is_to_the   
20     19    230           19_lib_the_to_on   
21     20    218           20_to_the_it_for   
22     21    213       21_modem_port_the_to   
23     22    212      22_db_windows_dos_mov   
24     23    204    23_printer_print_hp_the   
25     24    168  24_dos_windows_server_for   
26     25    160            25_it_the_is_to   
27     26    142        26_windows_os_nt_is   
28     27    136          27_the_to_of_that   

                                       Representation  \
0       [ax, max, the, to, of, is, and, it, in, that]   
1     [of, the, that, to, is, god, and, in, not, you]   
2   [the, he, game, in, to, and, team, was, of, that]   
3       [the, to, and, it, car, you, in, for, is, on]   
4      [the, of, to, and, in, for, is, on, space, be]   
5     [the, to, that, of, and, in, it, was, they, he]   
6     [of, the, to, and, is, in, that, it, for, have]   
7   [the, to, key, be, of, that, is, it, and, clip...   
8      [for, the, and, with, to, mhz, is, it, of, or]   
9   [image, jpeg, and, for, to, the, is, of, you, ...   
10  [ken, ockey, _too_, accent, answer, ites, hriv...   
11  [00, 50, for, 10, 1st, 20, wolverine, and, the...   
12   [gun, the, of, to, and, in, that, you, is, guns]   
13  [card, monitor, the, video, it, with, to, have...   
14  [scsi, drive, ide, disk, drives, controller, t...   
15  [israel, the, of, israeli, to, in, that, arab,...   
16  [window, the, to, widget, is, and, openwindows...   
17  [that, of, the, homosexual, to, in, is, homose...   
18  [the, of, and, in, were, armenian, they, armen...   
19  [that, is, to, the, of, you, moral, it, not, o...   
20  [lib, the, to, on, server, x11r5, is, sun, and...   
21       [to, the, it, for, and, is, of, be, on, you]   
22  [modem, port, the, to, serial, and, for, it, f...   
23  [db, windows, dos, mov, bh, the, it, and, file...   
24  [printer, print, hp, the, to, it, and, deskjet...   
25  [dos, windows, server, for, xfree86, and, to, ...   
26   [it, the, is, to, and, of, that, you, on, light]   
27  [windows, os, nt, is, to, the, and, it, that, of]   
28  [the, to, of, that, in, and, kuwait, we, is, s...   

                                  Representative_Docs  
0   [Since electrical wiring questions do turn up ...  
1   [\n#Rick Anderson replied to my letter with......  
2   [\nI agree that Keenan is an excellent choice....  
3   [As promised, below is a personal critique of ...  
4   [Archive-name: cryptography-faq/part08\nLast-m...  
5   [THE WHITE HOUSE\n\n                    Office...  
6   [------------- cut here -----------------\n\n\...  
7   [Hmm, followup on my own posting... Well, who ...  
8   [Hello, I have a motherboard and a case for sa...  
9   [Archive-name: graphics/resources-list/part2\n...  
10  [Choose any or all of the following as an answ...  
11  [The following comics are for auction.  The hi...  
12  [[This is a co-authored report from two of us ...  
13  [I was wondering if anyone out there has had t...  
14  [\n[ First of all, please edit your po